In [1]:
import pandas as pd
job_id='dj-synhub-extraction-lkbi9fy6zepu8rcjuxqhjwkbld52wgt0-ouutovygqc'
df = pd.read_csv(f'../../extractions/{job_id}/result.csv')
df

source_name dateline  \
0                           Dow Jones Institutional News      NaN   
1       Securities and Exchange Commission (SEC) Filings      NaN   
2                                            PR Newswire      NaN   
3           Public Companies News and Documents via PUBT      NaN   
4                                      Canada Stockwatch      NaN   
...                                                  ...      ...   
223516  Securities and Exchange Commission (SEC) Filings      NaN   
223517      Public Companies News and Documents via PUBT      NaN   
223518                               Global Banking News      NaN   
223519  Securities and Exchange Commission (SEC) Filings      NaN   
223520                      Dow Jones Institutional News      NaN   

        ingestion_datetime currency_codes  \
0            1739355044000            NaN   
1            1743191927000            NaN   
2            1744722047000            NaN   
3            1731288771000            NaN   
4            1736895739000            NaN   
...                    ...            ...   
223516       1741210800000            NaN   
223517       1742297491000            NaN   
223518       1727705061000            NaN   
223519       1715978722000            NaN   
223520       1740060073000            NaN   

        company_codes_association_ticker_exchange  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   
...                                           ...   
223516                                        NaN   
223517                                        NaN   
223518                                        NaN   
223519                                        NaN   
223520                                        NaN   

                                                    title  \
0       Press Release: XPENG announces its official la...   
1       First Busey Corporation - Statement of Changes...   
2       PLAUD.AI Acquires YC-Backed StarJar to Power I...   
3       Shionogi & Co. Ltd. - SHIONOGI Story 2 :Busine...   
4       Torex Gold Provides 2025 Operational Guidance ...   
...                                                   ...   
223516  Coinbase Global Inc. - Statement of Changes in...   
223517  Almawave S.p.A. - Almawave and Oracle: strateg...   
223518       QNB’s share buyback gets regulatory approval   
223519  FNCB Bancorp Inc. - Amendment to Statement of ...   
223520  Form 8.3 - The Vanguard Group, Inc.: Spirent C...   

                                                  snippet  \
0       \n   -- XPENG officially enters the UK, streng...   
1       Access the original document here\n\nStatement...   
2       SAN FRANCISCO, April 15, 2025 /PRNewswire/ -- ...   
3       Access the original document here\n\nSHIONOGI ...   
4       (All amounts expressed in U.S. dollars unless ...   
...                                                   ...   
223516  Access the original document here\n\nStatement...   
223517  Access the original document here\n\nAlmawave ...   
223518  Qatar-based banking firm QNB Group has said th...   
223519  Access the original document here\n\nAmendment...   
223520                                                NaN   

       company_codes_lineage_ticker_exchange                         an  \
0                                        NaN  DJDN000020250212el2c001sa   
1                                        NaN  SAEXC00020250328el3s00cin   
2                                        NaN  PRN0000020250415el4f000cs   
3                                        NaN  LCDVP00020241111ekbb0020f   
4                                        NaN  CNSW000020250114el1e00ifx   
...                                      ...                        ...   
223516                                   NaN  S

## Initial preprocessing

In [2]:
## Dropping irrelevant cols
cols2drop=['dateline','currency_codes','availability_datetime', 'copyright', 'language_code','region_of_origin','byline','person_codes','publication_date','publisher_name','credit','art','document_type','modification_datetime','market_index_codes'] + [c for c in df.columns if c.endswith('_exchange')]
df = df.drop(columns=cols2drop, errors='ignore') 

## Converting dt
for dt_column in ["modification_date", 'modification_datetime',"ingestion_datetime", "publication_datetime","publication_date"]:
    if dt_column in df.columns:
        df[dt_column] = pd.to_datetime(df[dt_column], unit='ms')

## Aggregating different company codes columns
cc_columns = sorted([c for c in df.columns if c.startswith('company_codes')])
for col in cc_columns:
    df[col] = df[col].apply(lambda x: ','.join(list(set(x.lstrip(',').split(','))-{'',})) if isinstance(x, str) else x)
    df[col] = df[col].fillna("")#.apply(list)
df['all_company_codes'] = df[cc_columns].agg(lambda x: ','.join(x), axis=1).apply(lambda x: ','.join(sorted(list(set(x.split(','))-{''}))))

df = df.drop(columns=cc_columns, errors='ignore') 
df = df.rename(columns={'all_company_codes':'company_codes'})

## Ordering cols logically
columns = ['source_name','title','snippet','body','section','word_count','source_code','industry_codes','company_codes','subject_codes','publication_datetime','ingestion_datetime','modification_date','region_codes','an','action']
assert all([c in df.columns for c in columns]), f"Missing columns: {[c for c in columns if c not in df.columns]}"
df = df[columns]
df

source_name  \
0                           Dow Jones Institutional News   
1       Securities and Exchange Commission (SEC) Filings   
2                                            PR Newswire   
3           Public Companies News and Documents via PUBT   
4                                      Canada Stockwatch   
...                                                  ...   
223516  Securities and Exchange Commission (SEC) Filings   
223517      Public Companies News and Documents via PUBT   
223518                               Global Banking News   
223519  Securities and Exchange Commission (SEC) Filings   
223520                      Dow Jones Institutional News   

                                                    title  \
0       Press Release: XPENG announces its official la...   
1       First Busey Corporation - Statement of Changes...   
2       PLAUD.AI Acquires YC-Backed StarJar to Power I...   
3       Shionogi & Co. Ltd. - SHIONOGI Story 2 :Busine...   
4       Torex Gold Provides 2025 Operational Guidance ...   
...                                                   ...   
223516  Coinbase Global Inc. - Statement of Changes in...   
223517  Almawave S.p.A. - Almawave and Oracle: strateg...   
223518       QNB’s share buyback gets regulatory approval   
223519  FNCB Bancorp Inc. - Amendment to Statement of ...   
223520  Form 8.3 - The Vanguard Group, Inc.: Spirent C...   

                                                  snippet  \
0       \n   -- XPENG officially enters the UK, streng...   
1       Access the original document here\n\nStatement...   
2       SAN FRANCISCO, April 15, 2025 /PRNewswire/ -- ...   
3       Access the original document here\n\nSHIONOGI ...   
4       (All amounts expressed in U.S. dollars unless ...   
...                                                   ...   
223516  Access the original document here\n\nStatement...   
223517  Access the original document here\n\nAlmawave ...   
223518  Qatar-based banking firm QNB Group has said th...   
223519  Access the original document here\n\nAmendment...   
223520                                                NaN   

                                                     body section  word_count  \
0       https://www.globenewswire.com/Tracker?data=06k...     NaN        1090   
1       FORM 4\n\nCheck this box if no longer subject ...     NaN         830   
2       PLAUD.AI: From Consumer Success to Enterprise ...     NaN         757   
3       SHIONOGI2Story\n\nSolving Social Issues throug...     NaN        3972   
4       TABLE 1: 2025 OPERATIONAL GUIDANCE\n\n        ...     NaN        4623   
...                                                   ...     ...         ...   
223516  FORM 4\n\nCheck this box if no longer subject ...     NaN        1307   
223517  ALMAWAVE AND ORACLE: STRATEGIC COLLABORATION\n...     NaN         996   
223518  Subject to market conditions, the program will...     NaN         192   
223519  Ownership Submission\n\nFORM 4/A\n\nCheck this...     NaN         677   
223520  \nThe Vanguard Group, Inc. ( ) \nForm 8.3 - Th...     NaN         997   

       source_code                                     industry_codes  \
0             DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
1            SAEXC                          ,i814,i81402,ibnk,ifinal,   
2              PRN  ,i1,i3302,i330202,i3302021,i3302022,i81502,i81...   
3            LCDVP  ,i257,i8395414,i951,ibcs,imedres,iphddd,iphhss...   
4             CNSW             ,i211,i22,ibasicm,igoldm,imet,infmore,   
...            ...                                                ...   
223516       SAEXC  ,i831,i83106,ibnk,icryxch,ifinal,ifmsoft,iinv,...   
223517       LCDVP      ,i3302,i330202,i3302021,i3302022,icomp,itech,   
223518      GLOBAN                          ,i814,i81402,ibnk,ifinal,   
223519       SAEXC                          ,i814,i81402,ibnk,ifinal,   
223520        DJDN        ,i3302,i3303,i831,i83108,ifinal,iinv,itech,   

        

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 223521 entries, 0 to 223520
Data columns (total 16 columns):
 #   Column                Non-Null Count   Dtype         
---  ------                --------------   -----         
 0   source_name           223521 non-null  object        
 1   title                 223521 non-null  object        
 2   snippet               205086 non-null  object        
 3   body                  223521 non-null  object        
 4   section               23957 non-null   object        
 5   word_count            223521 non-null  int64         
 6   source_code           223521 non-null  object        
 7   industry_codes        210216 non-null  object        
 8   company_codes         223521 non-null  object        
 9   subject_codes         223521 non-null  object        
 10  publication_datetime  223521 non-null  datetime64[ns]
 11  ingestion_datetime    223521 non-null  datetime64[ns]
 12  modification_date     223521 non-null  datetime64[ns]
 13 

### Decoding company names

In [4]:
from factiva.news.taxonomy import Taxonomy
user_key = 'LKbI9fY6ZEPU8RcJUxQHjwKbld52WGt0'
taxonomy = Taxonomy(user_key)
company_codes_df = taxonomy.get_category_codes('companies')
company_codes_df = company_codes_df[~company_codes_df.index.duplicated(keep='first')]
company_codes_df

description ticker ticker_exchange  \
code                                                                    
ISPETT                    Import Spetstorh Tov    NaN             NaN   
MSHARM                                   Mshak    NaN             NaN   
NOCSNO                      Nordic-Calista Llc    NaN             NaN   
XPKYTC     Xiapu Kunhai Yichen Trading Co. Ltd    NaN             NaN   
NZITSB                   Naza Italia Sdn. Bhd.    NaN             NaN   
...                                        ...    ...             ...   
BERTO                     Bertocchi Smallgoods    NaN             NaN   
GLBWIN                            GLOBAL WINES    NaN             NaN   
RNGASW                              Ringier Ag    NaN             NaN   
AAVBSA  Abs Alci Ve Blok Sanayi Anonim Sirketi    NaN             NaN   
FRMDEN                                  Farmco    NaN             NaN   

       exchange primary_exchange  
code                              
ISPETT      NaN              NaN  
MSHARM      NaN              NaN  
NOCSNO      NaN              NaN  
XPKYTC      NaN              NaN  
NZITSB      NaN              NaN  
...         ...              ...  
BERTO       NaN              NaN  
GLBWIN      NaN              NaN  
RNGASW      NaN              NaN  
AAVBSA      NaN              NaN  
FRMDEN      NaN              NaN  

[2000199 rows x 5 columns]

In [5]:
company_dict = company_codes_df.description.to_dict()
def extract_company_names(company_codes_list):
    company_codes_list = company_codes_list.upper().split(',')
    
    company_names = []
    for code in company_codes_list:
        if code in company_dict.keys():
            company_name = company_dict.get(code,code)
            company_names.append(company_name)
        else:
            company_names.append(code)
    return ','.join(company_names)

df['company_names'] = df['company_codes'].apply(lambda x: extract_company_names(x))
df

source_name  \
0                           Dow Jones Institutional News   
1       Securities and Exchange Commission (SEC) Filings   
2                                            PR Newswire   
3           Public Companies News and Documents via PUBT   
4                                      Canada Stockwatch   
...                                                  ...   
223516  Securities and Exchange Commission (SEC) Filings   
223517      Public Companies News and Documents via PUBT   
223518                               Global Banking News   
223519  Securities and Exchange Commission (SEC) Filings   
223520                      Dow Jones Institutional News   

                                                    title  \
0       Press Release: XPENG announces its official la...   
1       First Busey Corporation - Statement of Changes...   
2       PLAUD.AI Acquires YC-Backed StarJar to Power I...   
3       Shionogi & Co. Ltd. - SHIONOGI Story 2 :Busine...   
4       Torex Gold Provides 2025 Operational Guidance ...   
...                                                   ...   
223516  Coinbase Global Inc. - Statement of Changes in...   
223517  Almawave S.p.A. - Almawave and Oracle: strateg...   
223518       QNB’s share buyback gets regulatory approval   
223519  FNCB Bancorp Inc. - Amendment to Statement of ...   
223520  Form 8.3 - The Vanguard Group, Inc.: Spirent C...   

                                                  snippet  \
0       \n   -- XPENG officially enters the UK, streng...   
1       Access the original document here\n\nStatement...   
2       SAN FRANCISCO, April 15, 2025 /PRNewswire/ -- ...   
3       Access the original document here\n\nSHIONOGI ...   
4       (All amounts expressed in U.S. dollars unless ...   
...                                                   ...   
223516  Access the original document here\n\nStatement...   
223517  Access the original document here\n\nAlmawave ...   
223518  Qatar-based banking firm QNB Group has said th...   
223519  Access the original document here\n\nAmendment...   
223520                                                NaN   

                                                     body section  word_count  \
0       https://www.globenewswire.com/Tracker?data=06k...     NaN        1090   
1       FORM 4\n\nCheck this box if no longer subject ...     NaN         830   
2       PLAUD.AI: From Consumer Success to Enterprise ...     NaN         757   
3       SHIONOGI2Story\n\nSolving Social Issues throug...     NaN        3972   
4       TABLE 1: 2025 OPERATIONAL GUIDANCE\n\n        ...     NaN        4623   
...                                                   ...     ...         ...   
223516  FORM 4\n\nCheck this box if no longer subject ...     NaN        1307   
223517  ALMAWAVE AND ORACLE: STRATEGIC COLLABORATION\n...     NaN         996   
223518  Subject to market conditions, the program will...     NaN         192   
223519  Ownership Submission\n\nFORM 4/A\n\nCheck this...     NaN         677   
223520  \nThe Vanguard Group, Inc. ( ) \nForm 8.3 - Th...     NaN         997   

       source_code                                     industry_codes  \
0             DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
1            SAEXC                          ,i814,i81402,ibnk,ifinal,   
2              PRN  ,i1,i3302,i330202,i3302021,i3302022,i81502,i81...   
3            LCDVP  ,i257,i8395414,i951,ibcs,imedres,iphddd,iphhss...   
4             CNSW             ,i211,i22,ibasicm,igoldm,imet,infmore,   
...            ...                                                ...   
223516       SAEXC  ,i831,i83106,ibnk,icryxch,ifinal,ifmsoft,iinv,...   
223517       LCDVP      ,i3302,i330202,i3302021,i3302022,icomp,itech,   
223518      GLOBAN                          ,i814,i81402,ibnk,ifinal,   
223519       SAEXC                          ,i814,i81402,ibnk,ifinal,   
223520        DJDN        ,i3302,i3303,i831,i83108,ifinal,iinv,itech,   

        

### Decoding industries

In [6]:
industries_df = taxonomy.get_category_codes('industries')
industries_mapping_dict = industries_df.description.to_dict()

def extract_industries(industry_codes_list):
    if pd.isna(industry_codes_list):
        return ''
    industry_codes_list = sorted(list(set(industry_codes_list.split(','))-{''}))
    
    industry_descriptions = []
    for code in industry_codes_list:
        if code in industries_mapping_dict.keys():
            industry_desc = industries_mapping_dict.get(code,code)
            industry_descriptions.append(industry_desc)
        else:
            industry_descriptions.append(code)
    return ','.join(industry_descriptions)
df['industries'] = df['industry_codes'].apply(lambda x: extract_industries(x))
df

source_name  \
0                           Dow Jones Institutional News   
1       Securities and Exchange Commission (SEC) Filings   
2                                            PR Newswire   
3           Public Companies News and Documents via PUBT   
4                                      Canada Stockwatch   
...                                                  ...   
223516  Securities and Exchange Commission (SEC) Filings   
223517      Public Companies News and Documents via PUBT   
223518                               Global Banking News   
223519  Securities and Exchange Commission (SEC) Filings   
223520                      Dow Jones Institutional News   

                                                    title  \
0       Press Release: XPENG announces its official la...   
1       First Busey Corporation - Statement of Changes...   
2       PLAUD.AI Acquires YC-Backed StarJar to Power I...   
3       Shionogi & Co. Ltd. - SHIONOGI Story 2 :Busine...   
4       Torex Gold Provides 2025 Operational Guidance ...   
...                                                   ...   
223516  Coinbase Global Inc. - Statement of Changes in...   
223517  Almawave S.p.A. - Almawave and Oracle: strateg...   
223518       QNB’s share buyback gets regulatory approval   
223519  FNCB Bancorp Inc. - Amendment to Statement of ...   
223520  Form 8.3 - The Vanguard Group, Inc.: Spirent C...   

                                                  snippet  \
0       \n   -- XPENG officially enters the UK, streng...   
1       Access the original document here\n\nStatement...   
2       SAN FRANCISCO, April 15, 2025 /PRNewswire/ -- ...   
3       Access the original document here\n\nSHIONOGI ...   
4       (All amounts expressed in U.S. dollars unless ...   
...                                                   ...   
223516  Access the original document here\n\nStatement...   
223517  Access the original document here\n\nAlmawave ...   
223518  Qatar-based banking firm QNB Group has said th...   
223519  Access the original document here\n\nAmendment...   
223520                                                NaN   

                                                     body section  word_count  \
0       https://www.globenewswire.com/Tracker?data=06k...     NaN        1090   
1       FORM 4\n\nCheck this box if no longer subject ...     NaN         830   
2       PLAUD.AI: From Consumer Success to Enterprise ...     NaN         757   
3       SHIONOGI2Story\n\nSolving Social Issues throug...     NaN        3972   
4       TABLE 1: 2025 OPERATIONAL GUIDANCE\n\n        ...     NaN        4623   
...                                                   ...     ...         ...   
223516  FORM 4\n\nCheck this box if no longer subject ...     NaN        1307   
223517  ALMAWAVE AND ORACLE: STRATEGIC COLLABORATION\n...     NaN         996   
223518  Subject to market conditions, the program will...     NaN         192   
223519  Ownership Submission\n\nFORM 4/A\n\nCheck this...     NaN         677   
223520  \nThe Vanguard Group, Inc. ( ) \nForm 8.3 - Th...     NaN         997   

       source_code                                     industry_codes  \
0             DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
1            SAEXC                          ,i814,i81402,ibnk,ifinal,   
2              PRN  ,i1,i3302,i330202,i3302021,i3302022,i81502,i81...   
3            LCDVP  ,i257,i8395414,i951,ibcs,imedres,iphddd,iphhss...   
4             CNSW             ,i211,i22,ibasicm,igoldm,imet,infmore,   
...            ...                                                ...   
223516       SAEXC  ,i831,i83106,ibnk,icryxch,ifinal,ifmsoft,iinv,...   
223517       LCDVP      ,i3302,i330202,i3302021,i3302022,icomp,itech,   
223518      GLOBAN                          ,i814,i81402,ibnk,ifinal,   
223519       SAEXC                          ,i814,i81402,ibnk,ifinal,   
223520        DJDN        ,i3302,i3303,i831,i83108,ifinal,iinv,itech,   

        

### Partitioned Saving to parquet

In [ ]:
df["pub_date"] = pd.to_datetime(df["publication_datetime"])
df["year"]     = df["pub_date"].dt.year
df["month"]    = df["pub_date"].dt.month

df.to_parquet(
    f"../../extractions/{job_id}/parquet_dataset/",                # becomes a directory
    engine="pyarrow",
    partition_cols=["year", "month"],  # creates hive-style folders …/year=2025/month=2/
    row_group_size=256_000,            # ~256k rows per row-group is a sweet spot
    compression="zstd"
)

: 

## Splitting long articles
* Given volume and potential hardware limitations/speed considerations - TextTilingTokenizer seems [a good choice](https://medium.com/blue-orange-digital/document-chunking-guided-journey-a-greedy-start-e39a1dff15c3)

In [ ]:

import os, re
import pandas as pd
from bs4 import BeautifulSoup
from nltk.tokenize import TextTilingTokenizer
from joblib import Parallel, delayed
from tqdm_joblib import tqdm_joblib          # <-- already in requirements
from tqdm.auto import tqdm

TOKEN_RX = re.compile(r"[A-Za-z0-9]+(?:'[A-Za-z0-9]+)?")

def _segment_chunk(bodies: list[str],
                wcs:    list[int],
                wc_min: int):
    """
    Runs inside ONE worker process.
    Keeps a tokenizer alive for the whole chunk.
    """
    tok = TextTilingTokenizer()
    seg_chunk, err_chunk = [], []
    for body, wc in zip(bodies, wcs):
        if wc < wc_min:
            seg_chunk.append([body]); err_chunk.append(False); continue
        try:
            seg_chunk.append(tok.tokenize(body)); err_chunk.append(False)
        except Exception:
            seg_chunk.append([body]); err_chunk.append(True)
    return seg_chunk, err_chunk

def parallel_segment(df: pd.DataFrame,
                wc_min: int = 100,
                chunk_rows: int = 512,
                n_jobs: int | None = None):
    """
    Segment articles with far less IPC & per-call overhead.
    """
    n_jobs = n_jobs or max(os.cpu_count() - 1, 1)

    # split the dataframe indices into equal-sized chunks
    idx = list(range(len(df)))
    chunks = [idx[i:i + chunk_rows] for i in range(0, len(idx), chunk_rows)]
    total_chunks = len(chunks)

    # Prepare generator of Delayed objects (lazy parallel calls)
    delayed_calls = (
        delayed(_segment_chunk)(
            df.loc[c, "body"].tolist(), df.loc[c, "word_count"].tolist(), wc_min
        )
        for c in chunks
    )

    segments, errors = [], []  # will collect across chunks
    
    pbar = tqdm(total=total_chunks, desc="Segmenting (chunks)")
    results_iter = Parallel(
            n_jobs=n_jobs,
            backend="loky",
            prefer="processes",
            batch_size=4,
            return_as="generator_unordered",  # ✔ streams each chunk as it finishes
        )(delayed_calls)
    for seg_chunk, err_chunk in results_iter:
        segments.extend(seg_chunk)
        errors.extend(err_chunk)
        pbar.update()
    pbar.close()


    df_out = df.assign(
        segments     = segments,
        num_segments = [len(s) for s in segments]
    )
    return df_out, sum(errors)

In [ ]:
df

source_name  \
0                           Dow Jones Institutional News   
1       Securities and Exchange Commission (SEC) Filings   
2                                            PR Newswire   
3           Public Companies News and Documents via PUBT   
4                                      Canada Stockwatch   
...                                                  ...   
223516  Securities and Exchange Commission (SEC) Filings   
223517      Public Companies News and Documents via PUBT   
223518                               Global Banking News   
223519  Securities and Exchange Commission (SEC) Filings   
223520                      Dow Jones Institutional News   

                                                    title  \
0       Press Release: XPENG announces its official la...   
1       First Busey Corporation - Statement of Changes...   
2       PLAUD.AI Acquires YC-Backed StarJar to Power I...   
3       Shionogi & Co. Ltd. - SHIONOGI Story 2 :Busine...   
4       Torex Gold Provides 2025 Operational Guidance ...   
...                                                   ...   
223516  Coinbase Global Inc. - Statement of Changes in...   
223517  Almawave S.p.A. - Almawave and Oracle: strateg...   
223518       QNB’s share buyback gets regulatory approval   
223519  FNCB Bancorp Inc. - Amendment to Statement of ...   
223520  Form 8.3 - The Vanguard Group, Inc.: Spirent C...   

                                                  snippet  \
0       \n   -- XPENG officially enters the UK, streng...   
1       Access the original document here\n\nStatement...   
2       SAN FRANCISCO, April 15, 2025 /PRNewswire/ -- ...   
3       Access the original document here\n\nSHIONOGI ...   
4       (All amounts expressed in U.S. dollars unless ...   
...                                                   ...   
223516  Access the original document here\n\nStatement...   
223517  Access the original document here\n\nAlmawave ...   
223518  Qatar-based banking firm QNB Group has said th...   
223519  Access the original document here\n\nAmendment...   
223520                                                NaN   

                                                     body section  word_count  \
0       https://www.globenewswire.com/Tracker?data=06k...     NaN        1090   
1       FORM 4\n\nCheck this box if no longer subject ...     NaN         830   
2       PLAUD.AI: From Consumer Success to Enterprise ...     NaN         757   
3       SHIONOGI2Story\n\nSolving Social Issues throug...     NaN        3972   
4       TABLE 1: 2025 OPERATIONAL GUIDANCE\n\n        ...     NaN        4623   
...                                                   ...     ...         ...   
223516  FORM 4\n\nCheck this box if no longer subject ...     NaN        1307   
223517  ALMAWAVE AND ORACLE: STRATEGIC COLLABORATION\n...     NaN         996   
223518  Subject to market conditions, the program will...     NaN         192   
223519  Ownership Submission\n\nFORM 4/A\n\nCheck this...     NaN         677   
223520  \nThe Vanguard Group, Inc. ( ) \nForm 8.3 - Th...     NaN         997   

       source_code                                     industry_codes  \
0             DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
1            SAEXC                          ,i814,i81402,ibnk,ifinal,   
2              PRN  ,i1,i3302,i330202,i3302021,i3302022,i81502,i81...   
3            LCDVP  ,i257,i8395414,i951,ibcs,imedres,iphddd,iphhss...   
4             CNSW             ,i211,i22,ibasicm,igoldm,imet,infmore,   
...            ...                                                ...   
223516       SAEXC  ,i831,i83106,ibnk,icryxch,ifinal,ifmsoft,iinv,...   
223517       LCDVP      ,i3302,i330202,i3302021,i3302022,icomp,itech,   
223518      GLOBAN                          ,i814,i81402,ibnk,ifinal,   
223519       SAEXC                          ,i814,i81402,ibnk,ifinal,   
223520        DJDN        ,i3302,i3303,i831,i83108,ifinal,iinv,itech,   

        

In [16]:
import time, psutil
t0 = time.perf_counter()
df, errs = parallel_segment(df[:10000], chunk_rows=64)
print(f"{time.perf_counter()-t0:0.1f}s, peak RAM ≈ {psutil.Process().memory_info().rss/1e9:0.2f} GB")
print(f"{errs} documents raised an error during tiling.")
df_exploded = df.explode("segments")

Segmenting (chunks):   0%|          | 0/157 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [ ]:
# def factiva_wordcount(html: str) -> int:
#     """≈ Factiva ‘WC’ (±2 %)"""
#     return len(TOKEN_RX.findall(_strip_markup(html)))

# def _segment_worker(body: str, wc: int, wc_min: int = 100):
#     """Runs in a subprocess → create the tokenizer locally (it’s cheap)."""
#     if wc < wc_min:
#         return [body], False                  # no segmentation needed
#     try:
#         return TextTilingTokenizer().tokenize(body), False
#     except Exception:                         # rare: badly-formed text
#         return [body], True
    
# def parallel_segment(df: pd.DataFrame,
#         n_jobs: int | None = None,
#         wc_min: int = 100,
#         batch_size: int = 32):
#     """
#     Parameters
#     ----------
#     df : DataFrame with columns 'body' and 'word_count'
#     n_jobs : CPUs to use (default = all-1)
#     wc_min : skip tiling for very short docs
#     batch_size : joblib batch size (larger → fewer IPC hops)

#     Returns
#     -------
#     df_out : original DataFrame + 'segments' + 'num_segments'
#     err_cnt : int, docs that raised exceptions in TextTiling
#     """
#     n_jobs = n_jobs or max(os.cpu_count() - 1, 1)

#     # tqdm over the generator keeps RAM flat and progress accurate
#     gen = ((row.body, row.word_count) for row in df.itertuples(index=False))
#     with tqdm_joblib(total=len(df), desc="Segmenting") as pbar:
#         results = Parallel(
#             n_jobs=n_jobs,
#             backend="loky",       # robust, true multiprocessing
#             batch_size=batch_size,
#             prefer="processes",
#         )(delayed(_segment_worker)(b, wc, wc_min) for b, wc in gen
#         )
#         for _ in results:         # tick the progress bar after the fact
#             pbar.update()

#     segments, errs = map(list, zip(*results))
#     df_out = df.assign(
#         segments      = segments,
#         num_segments  = [len(s) for s in segments]
#     )
#     return df_out, sum(errs)

# df, errors = parallel_segment(df)
# print(f"{errors} documents raised an error during tiling.")

# df_exploded = df.explode("segments")

### Hashing and dedup
* How to drop duplicates without over-relying on Transformers? -> all sorts of hashing


In [11]:
df_exploded = pd.read_parquet(f'../../extractions/{job_id}/result_tiled.parquet')
df_exploded

source_name  \
0      Dow Jones Institutional News   
1      Dow Jones Institutional News   
2      Dow Jones Institutional News   
3      Dow Jones Institutional News   
4      Dow Jones Institutional News   
...                             ...   
13996  Dow Jones Institutional News   
13997  Dow Jones Institutional News   
13998  Dow Jones Institutional News   
13999  Dow Jones Institutional News   
14000  Dow Jones Institutional News   

                                                   title  \
0      Press Release: XPENG announces its official la...   
1      Press Release: XPENG announces its official la...   
2      Press Release: XPENG announces its official la...   
3      Press Release: XPENG announces its official la...   
4      Press Release: XPENG announces its official la...   
...                                                  ...   
13996  Press Release: Sun Communities, Inc. Announces...   
13997  Press Release: Sun Communities, Inc. Announces...   
13998  Press Release: Sun Communities, Inc. Announces...   
13999  Press Release: Sun Communities, Inc. Announces...   
14000  Press Release: Sun Communities, Inc. Announces...   

                                                 snippet  \
0      \n   -- XPENG officially enters the UK, streng...   
1      \n   -- XPENG officially enters the UK, streng...   
2      \n   -- XPENG officially enters the UK, streng...   
3      \n   -- XPENG officially enters the UK, streng...   
4      \n   -- XPENG officially enters the UK, streng...   
...                                                  ...   
13996  Sun Communities, Inc. Announces Restructuring ...   
13997  Sun Communities, Inc. Announces Restructuring ...   
13998  Sun Communities, Inc. Announces Restructuring ...   
13999  Sun Communities, Inc. Announces Restructuring ...   
14000  Sun Communities, Inc. Announces Restructuring ...   

                                                    body section  word_count  \
0      https://www.globenewswire.com/Tracker?data=06k...    None        1090   
1      https://www.globenewswire.com/Tracker?data=06k...    None        1090   
2      https://www.globenewswire.com/Tracker?data=06k...    None        1090   
3      https://www.globenewswire.com/Tracker?data=06k...    None        1090   
4      https://www.globenewswire.com/Tracker?data=06k...    None        1090   
...                                                  ...     ...         ...   
13996  Southfield, MI, Nov. 06, 2024 (GLOBE NEWSWIRE)...    None        1131   
13997  Southfield, MI, Nov. 06, 2024 (GLOBE NEWSWIRE)...    None        1131   
13998  Southfield, MI, Nov. 06, 2024 (GLOBE NEWSWIRE)...    None        1131   
13999  Southfield, MI, Nov. 06, 2024 (GLOBE NEWSWIRE)...    None        1131   
14000  Southfield, MI, Nov. 06, 2024 (GLOBE NEWSWIRE)...    None        1131   

      source_code                                     industry_codes  \
0            DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
1            DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
2            DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
3            DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
4            DJDN  ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
...           ...                                                ...   
13996        DJDN  ,i81502,i8150206,i815020602,i85,icre,ifinal,ii...   
13997        DJDN  ,i81502,i8150206,i815020602,i85,icre,ifinal,ii...   
13998        DJDN  ,i81502,i8150206,i815020602,i85,icre,ifinal,ii...   
13999        DJDN  ,i81502,i8150206,i815020602,i85,icre,ifinal,ii...   
14000        DJDN  ,i81502,i8150206,i815020602,i85,icre,ifinal,ii...   

                                           company_codes  \
0      bp,hkexch,hsflia,imotol,inmot,isuzu,mitmot,myj...   
1      bp,hkexch,hsflia,imotol,inmot,isuzu,mitmot,myj...   
2      bp,hkexch,hsflia,imotol,inmot,isuzu,mitmot,myj...   
3      bp,hkexch,hsflia,imotol,inmot,isuzu,mitm

In [ ]:
## requirements: datasketch, simhash
import hashlib

from collections import defaultdict
from typing import Dict, Iterable, List, Set

from datasketch import MinHash, MinHashLSH
from simhash import Simhash, SimhashIndex


re_ws  = re.compile(r"\s+")

df_exploded["segment_norm"] = (
    df_exploded["segments"]
      .str.lower()
      .str.replace(re_ws, " ", regex=True) 
      .str.strip()
)

# 2 — hash (still a Python loop but the strings are now short & tidy)
df_exploded["segment_hash"] = df_exploded["segment_norm"].map(
        lambda t: hashlib.md5(t.encode()).hexdigest()
)
print(df_exploded['segment_hash'].nunique(), df_exploded['segments'].nunique(), df_exploded['segments'].nunique()/df_exploded['segment_hash'].nunique())
df_exploded.drop_duplicates(subset=['segment_hash'], inplace=True)
df_exploded.reset_index(inplace=True)
df_exploded

1756225 1776316 1.0114398781477316


index                                       source_name  \
0             0                      Dow Jones Institutional News   
1             0                      Dow Jones Institutional News   
2             0                      Dow Jones Institutional News   
3             0                      Dow Jones Institutional News   
4             0                      Dow Jones Institutional News   
...         ...                                               ...   
1756220  223517      Public Companies News and Documents via PUBT   
1756221  223518                               Global Banking News   
1756222  223519  Securities and Exchange Commission (SEC) Filings   
1756223  223519  Securities and Exchange Commission (SEC) Filings   
1756224  223520                      Dow Jones Institutional News   

                                                     title  \
0        Press Release: XPENG announces its official la...   
1        Press Release: XPENG announces its official la...   
2        Press Release: XPENG announces its official la...   
3        Press Release: XPENG announces its official la...   
4        Press Release: XPENG announces its official la...   
...                                                    ...   
1756220  Almawave S.p.A. - Almawave and Oracle: strateg...   
1756221       QNB’s share buyback gets regulatory approval   
1756222  FNCB Bancorp Inc. - Amendment to Statement of ...   
1756223  FNCB Bancorp Inc. - Amendment to Statement of ...   
1756224  Form 8.3 - The Vanguard Group, Inc.: Spirent C...   

                                                   snippet  \
0        \n   -- XPENG officially enters the UK, streng...   
1        \n   -- XPENG officially enters the UK, streng...   
2        \n   -- XPENG officially enters the UK, streng...   
3        \n   -- XPENG officially enters the UK, streng...   
4        \n   -- XPENG officially enters the UK, streng...   
...                                                    ...   
1756220  Access the original document here\n\nAlmawave ...   
1756221  Qatar-based banking firm QNB Group has said th...   
1756222  Access the original document here\n\nAmendment...   
1756223  Access the original document here\n\nAmendment...   
1756224                                                NaN   

                                                      body section  \
0        https://www.globenewswire.com/Tracker?data=06k...     NaN   
1        https://www.globenewswire.com/Tracker?data=06k...     NaN   
2        https://www.globenewswire.com/Tracker?data=06k...     NaN   
3        https://www.globenewswire.com/Tracker?data=06k...     NaN   
4        https://www.globenewswire.com/Tracker?data=06k...     NaN   
...                                                    ...     ...   
1756220  ALMAWAVE AND ORACLE: STRATEGIC COLLABORATION\n...     NaN   
1756221  Subject to market conditions, the program will...     NaN   
1756222  Ownership Submission\n\nFORM 4/A\n\nCheck this...     NaN   
1756223  Ownership Submission\n\nFORM 4/A\n\nCheck this...     NaN   
1756224  \nThe Vanguard Group, Inc. ( ) \nForm 8.3 - Th...     NaN   

         word_count source_code  \
0              1090        DJDN   
1              1090        DJDN   
2              1090        DJDN   
3              1090        DJDN   
4              1090        DJDN   
...             ...         ...   
1756220         996       LCDVP   
1756221         192      GLOBAN   
1756222         677       SAEXC   
1756223         677       SAEXC   
1756224         997        DJDN   

                                            industry_codes  \
0        ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
1        ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
2        ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
3        ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
4        ,i3302022,i351,i35101,i35104,i64,i651,i654,iau...   
...                                                    ..

In [ ]:
df_exploded.to_parquet(f'../../extractions/{job_id}/result_exploded.parquet', index=False, engine='pyarrow')

In [ ]:
import numpy as np

NON_WORD_RE = re.compile(r"\W+")
TRANS_TABLE = str.maketrans({i: ' ' for i in range(256) if not chr(i).isalnum()})

def shingles(text: str, n: int = 8) -> list[str]:
    """Regex-based shingles (original)."""
    tokens = NON_WORD_RE.sub(' ', text).lower().split()
    return [' '.join(tokens[i:i+n]) for i in range(max(0, len(tokens)-n+1))]

class UnionFind:
    def __init__(self, n: int):
        self.parent = np.arange(n, dtype=np.int32)
        self.size = np.ones(n, dtype=np.int32)

    def find(self, x: int) -> int:
        while self.parent[x] != x:
            self.parent[x] = self.parent[self.parent[x]]
            x = self.parent[x]
        return x

    def union(self, a: int, b: int) -> None:
        ra, rb = self.find(a), self.find(b)
        if ra == rb:
            return
        if self.size[ra] < self.size[rb]:
            ra, rb = rb, ra
        self.parent[rb] = ra
        self.size[ra] += self.size[rb]

In [ ]:
def minhash_dedup(
    df: pd.DataFrame,
    col: str = "segment_norm",
    num_perm: int = 64,
    jaccard_thresh: float = 0.9,
    n_jobs: int = -1,
) -> Dict[int, List[int]]:
    """Cluster near‑identical texts using MinHash‑LSH (fast, parallel)."""

    df = df.reset_index(drop=True)
    n = len(df)

    # 3.1  Parallel signature build
    def _build(idx: int, txt: str):
        mh = MinHash(num_perm=num_perm)
        for sh in shingles(txt, 8):
            mh.update(sh.encode())
        return idx, mh

    mhs: List[MinHash] = [None] * n  # placeholder list
    with tqdm_joblib(tqdm(total=n, unit="docs", desc="MinHash build")):
        for idx, mh in Parallel(n_jobs=n_jobs)(
            delayed(_build)(i, t) for i, t in enumerate(df[col])
        ):
            mhs[idx] = mh

    # 3.2  Bulk LSH insert  (requires datasketch >= 1.6)
    lsh = MinHashLSH(threshold=jaccard_thresh, num_perm=num_perm)
    lsh.insert_bulk([str(i) for i in range(n)], mhs)

    # 3.3  Query & union
    uf = UnionFind(n)
    for idx, mh in tqdm(enumerate(mhs), total=n, unit="docs", desc="LSH query"):
        for cand in lsh.query(mh):
            j = int(cand)
            if j > idx:
                uf.union(idx, j)

    # 3.4  Collect clusters
    clusters: Dict[int, List[int]] = {}
    for i in range(n):
        root = uf.find(i)
        clusters.setdefault(root, []).append(i)
    return clusters

def containment_dedup(
    df: pd.DataFrame,
    candidates: Iterable[int],
    col: str = "segment_norm",
    use_aho: bool = True,
    n_jobs: int = -1,
) -> Set[int]:
    """Remove texts that are *verbatim substrings* of longer ones."""

    texts = {i: df.at[i, col] for i in candidates}
    by_len = sorted(texts.items(), key=lambda kv: len(kv[1]))
    keep: Set[int] = set(texts)

    if use_aho:
        try:
            import ahocorasick
        except ImportError:
            use_aho = False

    if use_aho:
        A = ahocorasick.Automaton()
        for idx, pat in by_len:
            A.add_word(pat, idx)
        A.make_automaton()
        for idx_long, long_txt in tqdm(reversed(by_len), desc="Containment (Aho)"):
            for _, idx_short in A.iter(long_txt):
                if idx_short != idx_long and idx_short in keep:
                    keep.discard(idx_short)
        return keep

    # Fallback O(n^2) with joblib
    def _probe(j_pair):
        j, (idx_short, short_txt) = j_pair
        if idx_short not in keep:
            return idx_short, True
        for idx_long, long_txt in by_len[j + 1 :]:
            if idx_long in keep and short_txt in long_txt:
                return idx_short, False
        return idx_short, True

    res = Parallel(n_jobs=n_jobs)(delayed(_probe)(p) for p in enumerate(by_len[:-1]))
    for idx_short, ok in res:
        if not ok:
            keep.discard(idx_short)
    return keep


In [ ]:
import simhash
simhash.__version__  # type: ignore

AttributeError: module 'simhash' has no attribute '__version__'

In [ ]:


def union_find(n: int):
    """Classic union‑find / disjoint‑set with path compression & union‑by‑size."""
    parent = list(range(n))
    size = [1] * n

    def find(x):
        while parent[x] != x:
            parent[x] = parent[parent[x]]
            x = parent[x]
        return x

    def union(a, b):
        ra, rb = find(a), find(b)
        if ra == rb:
            return
        if size[ra] < size[rb]:
            ra, rb = rb, ra
        parent[rb] = ra
        size[ra] += size[rb]

    return parent, find, union

def minhash_dedup(
    df: pd.DataFrame,
    col: str = "segment_norm",
    num_perm: int = 128,
    jaccard_thresh: float = 0.9,
) -> Dict[int, List[int]]:
    """Return clusters {root_idx: [member_idxs …]} by MinHash‑LSH.@≥thresh"""

    lsh = MinHashLSH(threshold=jaccard_thresh, num_perm=num_perm)
    mhs: List[MinHash] = []

    # 0‑based reindex for contiguous union‑find
    df = df.reset_index(drop=True)

    def build_mh(args):
        idx, txt = args
        mh = MinHash(num_perm=num_perm)
        for sh in shingles(txt, n=8):
            mh.update(sh.encode())
        return idx, mh
    for idx, txt in tqdm(df[col].items(), desc="MinHash: build", unit="doc"):
        mh = MinHash(num_perm=num_perm)
        for sh in shingles(txt, n=8):
            mh.update(sh.encode())
        lsh.insert(str(idx), mh)
        mhs.append(mh)

    parent, find, union = union_find(len(mhs))

    for idx, mh in tqdm(enumerate(mhs), total=len(mhs), desc="MinHash: query", unit="doc"):
        for candidate in lsh.query(mh):
            j = int(candidate)
            if j <= idx:
                continue  # avoid self / duplicate pairs
            union(idx, j)

    clusters: Dict[int, List[int]] = defaultdict(list)
    for i in range(len(mhs)):
        clusters[find(i)].append(i)
    return clusters


def containment_dedup(
    df: pd.DataFrame,
    candidates: Iterable[int],
    col: str = "segment_norm",
) -> Set[int]:
    """Return the indices **to keep** after removing verbatim substrings.

    Strategy: sort survivors by length; for each *longer* doc scan shorter ones.
    Optional optimisation with Aho‑Corasick if pyahocorasick is installed.
    """

    try:
        import ahocorasick

        automaton = ahocorasick.Automaton()
        texts = {i: df.at[i, col] for i in candidates}
        # shorter → pattern, longer → search text
        by_len = sorted(texts.items(), key=lambda kv: len(kv[1]))
        keep: Set[int] = set(texts.keys())
        for i, (idx_i, pat) in enumerate(by_len):
            automaton.add_word(pat, (idx_i, pat))
        automaton.make_automaton()

        for idx_long, txt_long in reversed(by_len):
            for end_idx, (idx_short, _pat) in automaton.iter(txt_long):
                if idx_short == idx_long or idx_short not in keep:
                    continue
                keep.discard(idx_short)  # short text fully contained
        return keep

    except ImportError:
        # fallback O(n^2) – OK for ≤100k survivors
        texts = {i: df.at[i, col] for i in candidates}
        by_len = sorted(texts.items(), key=lambda kv: len(kv[1]))
        keep: Set[int] = set(texts.keys())
        for j in range(len(by_len)):
            idx_short, short_txt = by_len[j]
            if idx_short not in keep:
                continue
            for idx_long, long_txt in by_len[j + 1 :]:
                if idx_long not in keep:
                    continue
                if short_txt in long_txt:
                    keep.discard(idx_short)
                    break
        return keep
    
def simhash_dedup(
    df: pd.DataFrame,
    candidates: Iterable[int],
    col: str = "segment_norm",
    ngram: int = 4,
    hamming_thresh: int = 3,
) -> Set[int]:
    """Return indices to keep after near‑dup removal via SimHash64."""

    def tok4(text: str) -> List[str]:
        toks = re.sub(r"\W+", " ", text).lower().split()
        if len(toks) < ngram:
            return toks
        return [" ".join(toks[i : i + ngram]) for i in range(len(toks) - ngram + 1)]

    # Build SimhashIndex
    objs = [(str(i), Simhash(tok4(df.at[i, col]), f=64)) for i in candidates]
    index = SimhashIndex(objs, k=hamming_thresh)

    dup_ids: Set[int] = set()
    for doc_id, sim in objs:
        if int(doc_id) in dup_ids:
            continue
        near = index.get_near_dups(sim)
        for d in near:
            if d != doc_id:
                dup_ids.add(int(d))
    keep = {i for i in candidates if i not in dup_ids}
    return keep


In [ ]:
def deduplicate(df: pd.DataFrame, col: str = "segment_norm") -> pd.DataFrame:
    """Full three‑stage dedup; returns a *new* DataFrame of unique docs."""

    print("[1/3] MinHash clustering …")
    clusters = minhash_dedup(df, col)
    canon_indices = {
        max(idxs, key=lambda i: len(df.at[i, col])) for idxs in clusters.values()
    }

    print("[2/3] Substring containment filter …")
    canon_indices = containment_dedup(df, canon_indices, col)

    print("[3/3] SimHash fuzzy filter …")
    canon_indices = simhash_dedup(df, canon_indices, col)

    return df.loc[sorted(canon_indices)].reset_index(drop=True)

: 

In [ ]:
df_deduped = deduplicate(df_exploded, col="segment_norm")

[1/3] MinHash clustering …


MinHash: build: 0doc [00:00, ?doc/s]

MinHash: query:   0%|          | 0/1756225 [00:00<?, ?doc/s]

[2/3] Substring containment filter …


In [ ]:
df_deduped['segment_word_count'] = df_deduped['segments'].progress_apply(lambda x: factiva_wordcount(x))
df_deduped

  0%|          | 0/146962 [00:00<?, ?it/s]

index        source_name  \
0           0      The Telegraph   
1           0      The Telegraph   
2           0      The Telegraph   
3           0      The Telegraph   
4           0      The Telegraph   
...       ...                ...   
146957  46675  walesonline.co.uk   
146958  46676  walesonline.co.uk   
146959  46676  walesonline.co.uk   
146960  46676  walesonline.co.uk   
146961  46676  walesonline.co.uk   

                                                    title  \
0       Global insurers pick India ally: Prudential pa...   
1       Global insurers pick India ally: Prudential pa...   
2       Global insurers pick India ally: Prudential pa...   
3       Global insurers pick India ally: Prudential pa...   
4       Global insurers pick India ally: Prudential pa...   
...                                                   ...   
146957  Financial services firm that collapsed owing c...   
146958  One of Cardiff's biggest employers is moving t...   
146959  One of Cardiff's biggest employers is moving t...   
146960  One of Cardiff's biggest employers is moving t...   
146961  One of Cardiff's biggest employers is moving t...   

                                                  snippet  \
0       'India is a key market for Prudential, and we ...   
1       'India is a key market for Prudential, and we ...   
2       'India is a key market for Prudential, and we ...   
3       'India is a key market for Prudential, and we ...   
4       'India is a key market for Prudential, and we ...   
...                                                   ...   
146957  Neal Griffith was chief executive of Optima Wo...   
146958  Car financing firm MotoNovo is moving its HQ f...   
146959  Car financing firm MotoNovo is moving its HQ f...   
146960  Car financing firm MotoNovo is moving its HQ f...   
146961  Car financing firm MotoNovo is moving its HQ f...   

                                                     body            section  \
0       London-based multinational insurance and asset...                NaN   
1       London-based multinational insurance and asset...                NaN   
2       London-based multinational insurance and asset...                NaN   
3       London-based multinational insurance and asset...                NaN   
4       London-based multinational insurance and asset...                NaN   
...                                                   ...                ...   
146957  Mr Griffith is the former chief executive and ...         Rugby News   
146958  It is vacating around 70,000 sq ft of space at...  Latest Wales News   
146959  It is vacating around 70,000 sq ft of space at...  Latest Wales News   
146960  It is vacating around 70,000 sq ft of space at...  Latest Wales News   
146961  It is vacating around 70,000 sq ft of space at...  Latest Wales News   

        word_count source_code  \
0              578      ABPTEL   
1              578      ABPTEL   
2              578      ABPTEL   
3              578      ABPTEL   
4              578      ABPTEL   
...            ...         ...   
146957        1210    WALESONL   
146958         717    WALESONL   
146959         717    WALESONL   
146960         717    WALESONL   
146961         717    WALESONL   

                                           industry_codes  \
0                              ,i82,i82001,i82002,ifinal,   
1                              ,i82,i82001,i82002,ifinal,   
2                              ,i82,i82001,i82002,ifinal,   
3                              ,i82,i82001,i82002,ifinal,   
4                              ,i82,i82001,i82002,ifinal,   
...                                                   ...   
146957                            ,i836,iacc,ibcs,ifinal,   
146958  ,i814,i81402,i81404,i81501,i8150104,i831,ibnk,...   
146959  ,i814,i81402,i81404,i81501,i8150104,i831,ibnk,...   
146960  ,i814,i81402,i81404,i81501,i8150104,i831,ibnk,...   
146961  ,i814,i81402,i81404,i81501,i8150104,i831,ibnk,...   

      

In [ ]:
df_deduped.to_csv(f'../../extractions/{job_id}/result_deduped_wo_sem_sim.csv', index=False)

## Optional check: Semantic similarity

In [ ]:
#!pip install -U sentence-transformers faiss-gpu-cu12 [works on Linux with NVIDIA GPU, will not work on Mac/Windows, careful!]
# --------------------------------------------------------------------
# 4)  Semantic dedup that handles *long* (≤ 2k-word) segments
# --------------------------------------------------------------------
import math, numpy as np, pandas as pd
import faiss
from tqdm.auto import tqdm
from transformers import AutoTokenizer
from sentence_transformers import SentenceTransformer

TEXT_COL      = "segments"
MODEL_NAME    = "intfloat/multilingual-e5-large-instruct"
CHUNK_TOKENS  = 350           # window length
STRIDE        = 300           # overlap: CHUNK_TOKENS – STRIDE  (= 50 here)
COS_THRESHOLD = 0.95
BATCH_CHUNKS  = 512           

# ───────────────────  initialise model & tokenizer ───────────────────
model     = SentenceTransformer(MODEL_NAME, device="cuda")
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME, use_fast=True)
DIM       = model.get_sentence_embedding_dimension()

# ───────────────────  helper: chunk→embed→mean ───────────────────────
def embed_long(text: str) -> np.ndarray:
    """Mean-pool E5 embeddings of overlapping CHUNK_TOKENS windows."""
    # 1) tokenise once
    ids = tokenizer(text, add_special_tokens=False)["input_ids"]

    # 2) split into overlapping windows
    slices = [
        ids[i : i + CHUNK_TOKENS]
        for i in range(0, len(ids), STRIDE)
    ] or [ids]                          # edge-case: empty → keep one slice

    # 3) decode back to strings for ST encoder
    windows = tokenizer.batch_decode(slices, skip_special_tokens=True)

    # 4) encode windows in smaller sub-batches to fit GPU
    embs, out = [], None
    for s in range(0, len(windows), BATCH_CHUNKS):
        sub = windows[s : s + BATCH_CHUNKS]
        sub_emb = model.encode(
            sub,
            batch_size=len(sub),
            convert_to_numpy=True,
            normalize_embeddings=True,
            show_progress_bar=False,
        )
        embs.append(sub_emb)
    out = np.vstack(embs).mean(axis=0)
    # 5) re-normalise pooled vector → cosine ready
    out /= np.linalg.norm(out) + 1e-12
    return out.astype("float32")

# ────────────────────  encode whole DataFrame  ───────────────────────
texts = df_deduped[TEXT_COL].tolist()
doc_embs = np.empty((len(texts), DIM), dtype="float32")

for i, txt in enumerate(tqdm(texts, desc="Encoding long docs")):
    doc_embs[i] = embed_long(txt)

# ────────────────────  FAISS search & clustering  ────────────────────
index = faiss.IndexFlatIP(DIM)
index.add(doc_embs)

D, I = index.search(doc_embs, 2)  



In [ ]:
N = len(df_deduped)
pairs = []
for i, (sim, j) in tqdm(enumerate(zip(D[:, 1], I[:, 1]))):
    j = int(j)
    if 0 <= j < N and i != j and sim >= COS_THRESHOLD:
        pairs.append((i, j))

parent = list(range(len(df_deduped)))
size   = [1]*len(df_deduped)

def find(x):
    while parent[x] != x:
        parent[x] = parent[parent[x]]
        x = parent[x]
    return x

def union(a, b):
    ra, rb = find(a), find(b)
    if ra == rb:
        return
    if size[ra] < size[rb]:
        ra, rb = rb, ra
    parent[rb] = ra
    size[ra]  += size[rb]

for a, b in tqdm(pairs):
    union(a, b)
    
clusters = {}
for idx in tqdm(range(len(df_deduped))):
    clusters.setdefault(find(idx), []).append(idx)

keep_idx = {
    max(ids, key=lambda i: len(df_deduped.at[i, TEXT_COL]))
    for ids in clusters.values()
}

df_semantic = df_deduped.loc[sorted(keep_idx)].reset_index(drop=True)
print(f"Semantic dedup kept {len(df_semantic)} / {len(df_deduped)} rows")

## Exporting results

In [ ]:
df_semantic.to_csv(f'../../extractions/{job_id}/result_deduped_semantic.csv', index=False)

In [ ]:
# df.to_csv('../../extractions/dj-synhub-extraction-lkbi9fy6zepu8rcjuxqhjwkbld52wgt0-l0fy7lkzhf/preprocessing_result.csv', index=False, encoding='utf-8')

In [ ]:
df_deduped.rename(columns={'index':'original_index'}, inplace=True)
df_deduped.to_csv(f'../../extractions/{job_id}/preprocessing_result_deduped.csv', index=False, encoding='utf-8')